In [2]:
import pandas as pd
import numpy as np
import re
from datetime import datetime
from collections import defaultdict
from json import JSONDecodeError
from qwikidata.sparql import return_sparql_query_results # python library for working with sparql and linked data from WikiData
import time
from requests.exceptions import ChunkedEncodingError
import math
#from SPARQLWrapper import SPARQLWrapper, JSON # sparql query library
import ssl

# Explore csv

Meglio tenere il corso_codice perchè è la foreign key di DegreeProgrammes e CourseOfStudies (educational activities): serve per unire i due database per facilitare le relazioni successive. 

In [2]:
 # create first dataframe only using the specified columns 
dataDegree = pd.read_csv("DegreeProgrammes.csv", sep=",",
                    usecols=["annoaccademico", "corso_codice", "corso_descrizione", "url", "campus", "sededidattica", "ambiti", "tipologia", "durata", "internazionale", "internazionale_titolo", "accesso", "lingue"], encoding="utf-8")

# .pickle is a python serialization format for easy and quick read-write, and pandas supports it natively
dataDegree.to_pickle("00_first_Degree.pickle")

# the first table we have looks like this:
dataDegree.head()

corso_codice annoaccademico    corso_descrizione  \
0           659      2018/2019       Giurisprudenza   
1           660      2018/2019       Giurisprudenza   
2           881      2018/2019         Architettura   
3           884      2018/2019  Chimica industriale   
4           897      2018/2019  Direzione aziendale   

                                                 url   campus sededidattica  \
0  http://www.unibo.it/it/didattica/corsi-di-stud...  Bologna       Bologna   
1  http://www.unibo.it/it/didattica/corsi-di-stud...  Ravenna       Ravenna   
2  http://www.unibo.it/it/didattica/corsi-di-stud...   Cesena        Cesena   
3  http://www.unibo.it/it/didattica/corsi-di-stud...  Bologna       Bologna   
4  http://www.unibo.it/it/didattica/corsi-di-stud...  Bologna       Bologna   

                      ambiti                        tipologia  durata  \
0             Giurisprudenza  Laurea Magistrale a ciclo unico       5   
1             Giurisprudenza  Laurea Magistrale a ciclo unico       5   
2  Ingegneria e architettura  Laurea Magistrale a ciclo unico       5   
3                    Scienze                Laurea Magistrale       2   
4      Economia e management                Laurea Magistrale       2   

   internazionale                    internazionale_titolo            lingue  \
0           False                                      NaN          Italiano   
1           False                                      NaN          Italiano   
2           False                                      NaN          Italiano   
3            True  Titolo multiplo (solo alcuni curricula)          Italiano   
4            True                                      NaN  Italiano Inglese   

                                             accesso  
0       libero accesso con verifica delle conoscenze  
1       libero accesso con verifica delle conoscenze  
2                                      numero chiuso  
3  libero accesso con verifica dell'adeguatezza d...  
4                                      numero chiuso

In [3]:
#ora filtriamo il database originale selezionando solo l'ambito umanistico, quello che tratteremo nella nostra ontologia
#Poi, resettiamo l'index in modo che mi dia un nuovo ordine 

In [3]:
data_mask = dataDegree['ambiti'] == "Studi umanistici"
dataHumanitiesDegree = dataDegree[data_mask].reset_index(drop=True)
dataHumanitiesDegree.head()

corso_codice annoaccademico  \
0           956      2018/2019   
1           957      2018/2019   
2           962      2018/2019   
3           964      2018/2019   
4           966      2018/2019   

                                   corso_descrizione  \
0  Dams - discipline delle arti, della musica  e ...   
1                                          Filosofia   
2                                             Storia   
3                Antropologia culturale ed etnologia   
4      Cinema, televisione e produzione multimediale   

                                                 url   campus sededidattica  \
0  http://www.unibo.it/it/didattica/corsi-di-stud...  Bologna       Bologna   
1  http://www.unibo.it/it/didattica/corsi-di-stud...  Bologna       Bologna   
2  http://www.unibo.it/it/didattica/corsi-di-stud...  Bologna       Bologna   
3  http://www.unibo.it/it/didattica/corsi-di-stud...  Bologna       Bologna   
4  http://www.unibo.it/it/didattica/corsi-di-stud...  Bologna       Bologna   

             ambiti          tipologia  durata  internazionale  \
0  Studi umanistici             Laurea       3           False   
1  Studi umanistici             Laurea       3           False   
2  Studi umanistici             Laurea       3           False   
3  Studi umanistici  Laurea Magistrale       2           False   
4  Studi umanistici  Laurea Magistrale       2           False   

  internazionale_titolo    lingue  \
0                   NaN  Italiano   
1                   NaN  Italiano   
2                   NaN  Italiano   
3                   NaN  Italiano   
4                   NaN  Italiano   

                                             accesso  
0       libero accesso con verifica delle conoscenze  
1       libero accesso con verifica delle conoscenze  
2       libero accesso con verifica delle conoscenze  
3  libero accesso con verifica dell'adeguatezza d...  
4  libero accesso con verifica dell'adeguatezza d...

In [4]:
dataHumanitiesDegree.to_pickle("00_Humanities_Degree.pickle")

In [5]:
dataCourse = pd.read_csv("CoursesOfStudies.csv", sep=",",
                    usecols=["corso_codice", "materia_codice", "materia_descrizione"], encoding="utf-8")

dataCourse.to_pickle("00_first_Course.pickle")

dataCourse.head()

corso_codice materia_codice  \
0         8894          81644   
1         9222          85238   
2         8420          87462   
3         9222          85199   
4         8412          87608   

                                 materia_descrizione  
0  LABORATORY ON RENEWABLE RAW MATERIALS AND CIRC...  
1                                 BAYESIAN INFERENCE  
2                        HISTORY OF ECONOMIC THOUGHT  
3                                    SURVEY SAMPLING  
4            TECNOLOGIA E LEGISLAZIONE FARMACEUTICHE

In [6]:
dataHumanitiesDegree["corso_codice"] = dataHumanitiesDegree["corso_codice"].astype(str)
dataCourse["corso_codice"] = dataCourse["corso_codice"].astype(str)
dataCourse["materia_codice"] = dataCourse["materia_codice"].astype(str)
data = pd.merge(dataHumanitiesDegree, dataCourse, on="corso_codice", how="left")

In [7]:
data["Italian University"] = "University of Bologna"

In [8]:
data.to_pickle("00_data.pickle")
pd.set_option("display.max_rows", None)
data.head()

corso_codice annoaccademico  \
0          956      2018/2019   
1          956      2018/2019   
2          956      2018/2019   
3          956      2018/2019   
4          956      2018/2019   

                                   corso_descrizione  \
0  Dams - discipline delle arti, della musica  e ...   
1  Dams - discipline delle arti, della musica  e ...   
2  Dams - discipline delle arti, della musica  e ...   
3  Dams - discipline delle arti, della musica  e ...   
4  Dams - discipline delle arti, della musica  e ...   

                                                 url   campus sededidattica  \
0  http://www.unibo.it/it/didattica/corsi-di-stud...  Bologna       Bologna   
1  http://www.unibo.it/it/didattica/corsi-di-stud...  Bologna       Bologna   
2  http://www.unibo.it/it/didattica/corsi-di-stud...  Bologna       Bologna   
3  http://www.unibo.it/it/didattica/corsi-di-stud...  Bologna       Bologna   
4  http://www.unibo.it/it/didattica/corsi-di-stud...  Bologna       Bologna   

             ambiti tipologia  durata  internazionale internazionale_titolo  \
0  Studi umanistici    Laurea       3           False                   NaN   
1  Studi umanistici    Laurea       3           False                   NaN   
2  Studi umanistici    Laurea       3           False                   NaN   
3  Studi umanistici    Laurea       3           False                   NaN   
4  Studi umanistici    Laurea       3           False                   NaN   

     lingue                                       accesso materia_codice  \
0  Italiano  libero accesso con verifica delle conoscenze          13769   
1  Italiano  libero accesso con verifica delle conoscenze          27104   
2  Italiano  libero accesso con verifica delle conoscenze             45   
3  Italiano  libero accesso con verifica delle conoscenze          41822   
4  Italiano  libero accesso con verifica delle conoscenze          87329   

                              materia_descrizione     Italian University  
0                           ACUSTICA MUSICALE (1)  University of Bologna  
1                                ANALISI DEL FILM  University of Bologna  
2                          ANTROPOLOGIA CULTURALE  University of Bologna  
3  CINEMATOGRAFIA DOCUMENTARIA E SPERIMENTALE (1)  University of Bologna  
4            DIDATTICA DELLA STORIA DELL'ARTE (1)  University of Bologna

In [57]:
data = pd.read_pickle("00_data.pickle")

Ora, cerchiamo di incorporare i dati di un nuovo csv contenente gli SSD, i CFU e il CODICE CURRICULA degli insegnamenti, basandoci sul codice materia come chiave comune. 

In [58]:
SSDandCFU = pd.read_csv("DettagliCurriculaSSDeCFU.csv", sep=",",
                        usecols=["materia_codice", "insegnamento_ssd", "insegnamento_crediti"], encoding="utf-8")
#SSDandCFU["curriculum_codice"] = SSDandCFU["curriculum_codice"].astype(str)
SSDandCFU.head()

materia_codice insegnamento_ssd  insegnamento_crediti
0           222.0           IUS/08                  12.0
1         74764.0           IUS/01                  12.0
2           536.0           IUS/18                   8.0
3         24331.0           IUS/19                   8.0
4           230.0           IUS/13                   9.0

In [36]:
#newDB = SSDandCFU[SSDandCFU['curriculum_codice'].str.contains('2017') == False]

In [46]:
#DDD = newDB.drop(newDB.filter(regex='curriculum_codice').columns, axis=1)

In [65]:
DDD = SSDandCFU.drop_duplicates(subset=['materia_codice'], keep='first')

In [66]:
DDD["materia_codice"] = DDD["materia_codice"].astype(str)
DDD["insegnamento_crediti"] = DDD["insegnamento_crediti"].astype(str)
DDD.head()

materia_codice insegnamento_ssd insegnamento_crediti
425        85615.0           IUS/12                  2.0
444        81811.0           IUS/21                  7.0
493        74365.0           IUS/04                  7.0
495        81805.0           IUS/01                  7.0
496        81808.0           IUS/19                  7.0

In [67]:
def reformat_materia_codice(name):
    name = name.replace(".0", "")
    return name

In [68]:
DDD["materia_codice"] = DDD["materia_codice"].apply(reformat_materia_codice)
DDD["insegnamento_crediti"] = DDD["insegnamento_crediti"].apply(reformat_materia_codice)
DDD.head()

materia_codice insegnamento_ssd insegnamento_crediti
425          85615           IUS/12                    2
444          81811           IUS/21                    7
493          74365           IUS/04                    7
495          81805           IUS/01                    7
496          81808           IUS/19                    7

In [69]:
dataPlusCurricula = pd.merge(data, DDD, on="materia_codice", how="left")

In [70]:
pd.set_option("display.max_rows", None)
dataPlusCurricula.head(1800)

corso_codice annoaccademico  \
0             956      2018/2019   
1             956      2018/2019   
2             956      2018/2019   
3             956      2018/2019   
4             956      2018/2019   
5             956      2018/2019   
6             956      2018/2019   
7             956      2018/2019   
8             956      2018/2019   
9             956      2018/2019   
10            956      2018/2019   
11            956      2018/2019   
12            956      2018/2019   
13            956      2018/2019   
14            956      2018/2019   
15            956      2018/2019   
16            956      2018/2019   
17            956      2018/2019   
18            956      2018/2019   
19            956      2018/2019   
20            956      2018/2019   
21            956      2018/2019   
22            956      2018/2019   
23            956      2018/2019   
24            956      2018/2019   
25            956      2018/2019   
26            956      2018/2019   
27            956      2018/2019   
28            956      2018/2019   
29            956      2018/2019   
30            956      2018/2019   
31            956      2018/2019   
32            956      2018/2019   
33            956      2018/2019   
34            956      2018/2019   
35            956      2018/2019   
36            956      2018/2019   
37            956      2018/2019   
38            956      2018/2019   
39            956      2018/2019   
40            956      2018/2019   
41            956      2018/2019   
42            956      2018/2019   
43            956      2018/2019   
44            956      2018/2019   
45            956      2018/2019   
46            956      2018/2019   
47            956      2018/2019   
48            956      2018/2019   
49            956      2018/2019   
50            956      2018/2019   
51            956      2018/2019   
52            956      2018/2019   
53            956      2018/2019   
54            956      2018/2019   
55            956      2018/2019   
56            956      2018/2019   
57            956      2018/2019   
58            956      2018/2019   
59            956      2018/2019   
60            956      2018/2019   
61            956      2018/2019   
62            956      2018/2019   
63            956      2018/2019   
64            956      2018/2019   
65            956      2018/2019   
66            956      2018/2019   
67            956      2018/2019   
68            956      2018/2019   
69            956      2018/2019   
70            956      2018/2019   
71            956      2018/2019   
72            956      2018/2019   
73            956      2018/2019   
74            956      2018/2019   
75            956      2018/2019   
76            956      2018/2019   
77            956      2018/2019   
78            956      2018/2019   
79            956      2018/2019   
80            957      2018/2019   
81            957      2018/2019   
82            957      2018/2019   
83            957      2018/2019   
84            957      2018/2019   
85            957      2018/2019   
86            957      2018/2019   
87            957      2018/2019   
88            957      2018/2019   
89            957      2018/2019   
90            957      2018/2019   
91            957      2018/2019   
92            957      2018/2019   
93            957      2018/2019   
94            957      2018/2019   
95            957      2018/2019   
96            957      2018/2019   
97            957      2018/2019   
98            957      2018/2019   
99            957      2018/2019   
100           957      2018/2019   
101           957      2018/2019   
102           957      2018/2019   
103           957      2018/2019   
104           957      2018/2019   
105           957      2018/2019   
106           957      2018/2019   
107           957      2018/2019   
108           957      2018/2019   
109           957      2018/2019   
110      

In [ ]:
dataPlusCurricula.to_pickle("00_dataPlusCurricula.pickle")
dataPlusCurricula.head(500)

# COSE CHE MANCANO DA INTEGRARE
Ora, procediamo con integrare la DegreeClass e la DegreeClassDescription come ulteriori colonne del database, associate ad ogni codice corso. 

Valutare se integrare a mano gli indirizzi/curricula 

Riflettere sulla INTERNATIONALQualification e sugli individui di titolo congiunto O multiplo (aggiungere un ID?) 

Integrare classi di laurea e description di classi di laurea. 

Integrare type of educational activity: internship, laboratory, exam 


Dipartimenti? 


In [17]:
dataPlusCurricula.to_pickle("01_dataRename.pickle")

In [36]:
data = pd.read_pickle("01_dataRename.pickle")
data.head(500)

id academicYear                               DegreeProgrammeLabel  \
0    956    2018/2019  Dams - discipline delle arti, della musica  e ...   
1    956    2018/2019  Dams - discipline delle arti, della musica  e ...   
2    956    2018/2019  Dams - discipline delle arti, della musica  e ...   
3    956    2018/2019  Dams - discipline delle arti, della musica  e ...   
4    956    2018/2019  Dams - discipline delle arti, della musica  e ...   
5    956    2018/2019  Dams - discipline delle arti, della musica  e ...   
6    956    2018/2019  Dams - discipline delle arti, della musica  e ...   
7    956    2018/2019  Dams - discipline delle arti, della musica  e ...   
8    956    2018/2019  Dams - discipline delle arti, della musica  e ...   
9    956    2018/2019  Dams - discipline delle arti, della musica  e ...   
10   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
11   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
12   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
13   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
14   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
15   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
16   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
17   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
18   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
19   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
20   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
21   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
22   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
23   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
24   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
25   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
26   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
27   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
28   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
29   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
30   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
31   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
32   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
33   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
34   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
35   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
36   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
37   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
38   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
39   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
40   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
41   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
42   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
43   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
44   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
45   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
46   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
47   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
48   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
49   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
50   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
51   956    2018/2019  Dams - discipline delle arti, d

In [35]:
#rename columns
dataPlusCurricula.rename(columns = {'corso_codice':'id', 'annoaccademico':'academicYear', 'url':'DegreeProgramme', 'corso_descrizione':'DegreeProgrammeLabel', 'sededidattica':'PlaceOfTeaching', 'ambiti':'AcademicField', 'tipologia':'type', 'durata':'hasYearsOfDuration', 'internazionale':'International', 'internazionale_titolo':'InternationalQualification', 'lingue':'TeachingLanguage', 'accesso':'AccessType', 'materia_codice':'TeachingCode', 'materia_descrizione':'EducationalActivity', 'insegnamento_ssd' : 'Ssd', 'insegnamento_crediti' : 'Cfu'}, inplace = True)
dataPlusCurricula.head(500)


id academicYear                               DegreeProgrammeLabel  \
0    956    2018/2019  Dams - discipline delle arti, della musica  e ...   
1    956    2018/2019  Dams - discipline delle arti, della musica  e ...   
2    956    2018/2019  Dams - discipline delle arti, della musica  e ...   
3    956    2018/2019  Dams - discipline delle arti, della musica  e ...   
4    956    2018/2019  Dams - discipline delle arti, della musica  e ...   
5    956    2018/2019  Dams - discipline delle arti, della musica  e ...   
6    956    2018/2019  Dams - discipline delle arti, della musica  e ...   
7    956    2018/2019  Dams - discipline delle arti, della musica  e ...   
8    956    2018/2019  Dams - discipline delle arti, della musica  e ...   
9    956    2018/2019  Dams - discipline delle arti, della musica  e ...   
10   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
11   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
12   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
13   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
14   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
15   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
16   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
17   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
18   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
19   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
20   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
21   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
22   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
23   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
24   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
25   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
26   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
27   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
28   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
29   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
30   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
31   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
32   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
33   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
34   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
35   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
36   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
37   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
38   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
39   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
40   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
41   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
42   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
43   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
44   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
45   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
46   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
47   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
48   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
49   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
50   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
51   956    2018/2019  Dams - discipline delle arti, d

In [30]:
def degreeClass(value):
    degreeClassValue = ''
    if value == '956':
        degreeClassValue = 'L-3'
    elif value == '957':
        degreeClassValue = 'L-5'
    return degreeClassValue

In [34]:
dataPlusCurricula["DegreeClass"] = dataPlusCurricula["id"].apply(degreeClass)
dataPlusCurricula.head(800)

id academicYear                               DegreeProgrammeLabel  \
0    956    2018/2019  Dams - discipline delle arti, della musica  e ...   
1    956    2018/2019  Dams - discipline delle arti, della musica  e ...   
2    956    2018/2019  Dams - discipline delle arti, della musica  e ...   
3    956    2018/2019  Dams - discipline delle arti, della musica  e ...   
4    956    2018/2019  Dams - discipline delle arti, della musica  e ...   
5    956    2018/2019  Dams - discipline delle arti, della musica  e ...   
6    956    2018/2019  Dams - discipline delle arti, della musica  e ...   
7    956    2018/2019  Dams - discipline delle arti, della musica  e ...   
8    956    2018/2019  Dams - discipline delle arti, della musica  e ...   
9    956    2018/2019  Dams - discipline delle arti, della musica  e ...   
10   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
11   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
12   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
13   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
14   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
15   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
16   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
17   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
18   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
19   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
20   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
21   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
22   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
23   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
24   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
25   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
26   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
27   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
28   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
29   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
30   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
31   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
32   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
33   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
34   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
35   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
36   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
37   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
38   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
39   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
40   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
41   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
42   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
43   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
44   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
45   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
46   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
47   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
48   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
49   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
50   956    2018/2019  Dams - discipline delle arti, della musica  e ...   
51   956    2018/2019  Dams - discipline delle arti, d